In [3]:
import numpy as np
from scipy.fftpack import fft2, ifft2
import matplotlib.pyplot as plt
import imageio
import matplotlib as mpl

N =Nx=Ny= 201  # Grid size (for simplicity, using a square grid)
h = 0.01  # Spatial step
dt = 0.0001  # Initial time step
T = 0.01  # Total simulation time
alpha = [[0, 0.49], [-0.49, 0]]  
# Spatial domain
x = np.linspace(-1, 1, N)
y = np.linspace(-1, 1, N)
X, Y = np.meshgrid(x, y)
phi_1 = np.zeros((N, N))
phi_2 = np.zeros((N, N))
print(alpha[0])
a = alpha[0]
print (a[0])
c = {(1, 1): 0.2, (1, 2): 0.5, (2, 1): 0.1, (2, 2): 0.5}
chi = -0.2
chi_prime = 0.2
# Define the average compositions for phi_1 and phi_2
phi_avg = [0.35, 0.3]
# Generate random fields with specified average compositions
fields = []
for avg in phi_avg:
    # Create a field with random values around the specified average
    field = avg + 0.01 * np.random.randn(N, N)
    fields.append(field)
phi_1 = fields[0]  # Initializing with random values
phi_2 = fields[1]
mpl.rcParams['figure.dpi'] = 1600
# Visualize the fields
fig, axarr = plt.subplots(1, 2, figsize=(10, 4))
titles = ["phi_1, t=0", "phi_2,t=0"]
for i, field in enumerate(fields):
    im = axarr[i].imshow(field, cmap="RdBu_r")
    axarr[i].imshow(field, cmap="RdBu_r")
    axarr[i].set_title(titles[i])
    axarr[i].axis('off')
    fig.colorbar(im, ax=axarr[i], fraction=0.046, pad=0.04)

plt.tight_layout()
plt.savefig(f"T_$t=0$phi_chi_{chi}_alpha_{alpha}_chi'_{chi_prime}.png", dpi=200, bbox_inches='tight')
plt.show()
def generate_white_noise(Nx, Ny):
    """
    Generate white noise fields with zero mean and unit width.

    Parameters:
    - Nx, Ny: Dimensions of the 2D grid.

    Returns:
    - zeta1, zeta2: White noise fields.
    """

    #zeta1 = 0.000001* np.random.randn(Nx, Ny)
    #zeta2 = 0.000001* np.random.randn(Nx, Ny)
    gamma1 = 1.0e-5  # in units of inverse seconds, for particles in water
    gamma2 = 1.0e-5  # in units of inverse seconds, for particles in air

    kB= 1.38e-23
    T = 298
    kBT = 4.117e-10
    zeta1 = np.sqrt(2 * kBT * gamma1) * np.random.normal(size=(Nx, Ny))
    zeta2 = np.sqrt(2 * kBT * gamma1) * np.random.normal(size=(Nx, Ny))


    return zeta1, zeta2
def visualize_white_noise(zeta1, zeta2):
    """
    Visualize white noise fields.

    Parameters:
    - zeta1, zeta2: White noise fields to visualize.
    """

    fig, axarr = plt.subplots(1, 2, figsize=(10, 5))

    # Visualize zeta1
    c1 = axarr[0].imshow(zeta1, cmap='RdBu_r')
    axarr[0].set_title("$\\zeta_1$")
    fig.colorbar(c1, ax=axarr[0])

    # Visualize zeta2
    c2 = axarr[1].imshow(zeta2, cmap='RdBu_r')
    axarr[1].set_title("$\\zeta_2$")
    fig.colorbar(c2, ax=axarr[1])

    plt.tight_layout()
    plt.savefig(f"T_$t=0$zeata_chi_{chi}_alpha_{alpha}_chi'_{chi_prime}.png", dpi=200, bbox_inches='tight')
    plt.show()

zeta1, zeta2 = generate_white_noise(Nx, Ny)
visualize_white_noise(zeta1, zeta2)
kx = 2 * np.pi * np.fft.fftfreq(Nx, d=h)
ky = 2 * np.pi * np.fft.fftfreq(Ny, d=h)
KX, KY = np.meshgrid(kx, ky)

def fourier_transform(f):
    return fft2(f)

def inverse_fourier_transform(f):
    return ifft2(f)
#For binary mixture
def compute_equilibrium_chemical_potentials(phi_1, phi_2, c, chi, chi_prime):
    """
    Computes the equilibrium chemical potentials for a binary mixture.
    
    Parameters:
    - phi_1, phi_2: The scalar fields for components 1 and 2.
    - c: A dictionary with keys (i, j) that maps to the c_{i,j} values.
    - chi: Interaction parameter chi_{ij}.
    - chi_prime: Interaction parameter chi_prime.
    
    Returns:
    - mu_1_eq, mu_2_eq: The equilibrium chemical potentials for components 1 and 2.
    """

    # Calculating mu_1_eq
    term1_1 = 2 * (phi_1 - c[(1, 1)]) * (phi_1 - c[(1, 2)])
    term2_1 = 2 * phi_1 - c[(1, 1)] - c[(1, 2)]
    mu_1_eq = term1_1 * term2_1 + chi * phi_2 + 2 * chi_prime * phi_1 * phi_2**2

    # Calculating mu_2_eq
    term1_2 = 2 * (phi_2 - c[(2, 1)]) * (phi_2 - c[(2, 2)])
    term2_2 = 2 * phi_2 - c[(2, 1)] - c[(2, 2)]
    mu_2_eq = term1_2 * term2_2 + chi * phi_1 + 2 * chi_prime * phi_2 * phi_1**2
    

    return mu_1_eq, mu_2_eq
def compute_j_fourier(mu_1_k, mu_2_k, phi_1_k, phi_2_k, alpha, zeta_k_1, zeta_k_2):
    """
    Computes the Fourier-transformed fluxes based on the given Fourier-transformed variables.
    """

    j_1_k = -1j * KX * mu_1_k - alpha[0][0] * 1j * KX * phi_1_k - alpha[0][1] * 1j * KX * phi_2_k \
            - 1j * KY * mu_1_k - alpha[0][0] * 1j * KY * phi_1_k - alpha[0][1] * 1j * KY * phi_2_k + zeta_k_1
    
    j_2_k = -1j * KX * mu_2_k - alpha[1][0] * 1j * KX * phi_1_k - alpha[1][1] * 1j * KX * phi_2_k \
            - 1j * KY * mu_2_k - alpha[1][0] * 1j * KY * phi_1_k - alpha[1][1] * 1j * KY * phi_2_k + zeta_k_2

    return j_1_k, j_2_k
def rk4_step(phi_1_k, phi_2_k, mu_1_k, mu_2_k, dt, alpha, zeta_k_1, zeta_k_2):
    """
    Performs one step of the RK4 integration.
    """
    
    k1_1, k1_2 = compute_j_fourier(mu_1_k, mu_2_k, phi_1_k, phi_2_k, alpha, zeta_k_1, zeta_k_2)
    k2_1, k2_2 = compute_j_fourier(mu_1_k, mu_2_k, phi_1_k + 0.5 * dt * k1_1, phi_2_k + 0.5 * dt * k1_2, alpha, zeta_k_1, zeta_k_2)
    k3_1, k3_2 = compute_j_fourier(mu_1_k, mu_2_k, phi_1_k + 0.5 * dt * k2_1, phi_2_k + 0.5 * dt * k2_2, alpha, zeta_k_1, zeta_k_2)
    k4_1, k4_2 = compute_j_fourier(mu_1_k, mu_2_k, phi_1_k + dt * k3_1, phi_2_k + dt * k3_2, alpha, zeta_k_1, zeta_k_2)

    next_phi_1_k = phi_1_k + (dt/6.0) * (k1_1 + 2*k2_1 + 2*k3_1 + k4_1)
    next_phi_2_k = phi_2_k + (dt/6.0) * (k1_2 + 2*k2_2 + 2*k3_2 + k4_2)

    return next_phi_1_k, next_phi_2_k


def adams_moulton_step(phi_1_k, phi_2_k, mu_1_k, mu_2_k, alpha, zeta_k_1, zeta_k_2, prev_phi_ks, dt, compute_j_fourier, tol=1e-6, max_iter=1000):
    """
    Performs one step of the 4-step Adams-Moulton integration.
    Checks for convergence of the solution.
    """

    # Calculate the fluxes for the previous time steps
    j_prev_1, j_prev_2 = compute_j_fourier(mu_1_k, mu_2_k, prev_phi_ks[-1][0], prev_phi_ks[-1][1], alpha, zeta_k_1, zeta_k_2)
    j_prev2_1, j_prev2_2 = compute_j_fourier(mu_1_k, mu_2_k, prev_phi_ks[-2][0], prev_phi_ks[-2][1], alpha, zeta_k_1, zeta_k_2)
    j_prev3_1, j_prev3_2 = compute_j_fourier(mu_1_k, mu_2_k, prev_phi_ks[-3][0], prev_phi_ks[-3][1], alpha, zeta_k_1, zeta_k_2)

    # Initialize the guess for the future values
    phi_k_next_old = np.array([phi_1_k, phi_2_k])

    for iteration in range(max_iter):
        # Compute the flux for the guessed future value
        j_future_1, j_future_2 = compute_j_fourier(mu_1_k, mu_2_k, phi_k_next_old[0], phi_k_next_old[1], alpha, zeta_k_1, zeta_k_2)
        
        phi_1_k_next_new = phi_1_k + (dt/24.0) * (55*j_future_1 - 59*j_prev_1 + 37*j_prev2_1 - 9*j_prev3_1)
        phi_2_k_next_new = phi_2_k + (dt/24.0) * (55*j_future_2 - 59*j_prev_2 + 37*j_prev2_2 - 9*j_prev3_2)

        # Check convergence
        if np.linalg.norm(np.array([phi_1_k_next_new, phi_2_k_next_new]) - phi_k_next_old) < tol:
            break
        
        phi_k_next_old = np.array([phi_1_k_next_new, phi_2_k_next_new])

    return phi_1_k_next_new, phi_2_k_next_new



prev_phi_ks = []
t = 0
while t < T:
    # a. Compute the Equilibrium Chemical Potentials
    mu_1_eq, mu_2_eq = compute_equilibrium_chemical_potentials(phi_1, phi_2, c, chi, chi_prime)
    
    # b. Fourier Transform
    phi_1_k = fourier_transform(phi_1)
    phi_2_k = fourier_transform(phi_2)
    mu_1_eq_k = fourier_transform(mu_1_eq)
    mu_2_eq_k = fourier_transform(mu_2_eq)
    zeta1, zeta2 = generate_white_noise(Nx, Ny)
    zeta_k_1 = fourier_transform(zeta1)
    zeta_k_2 = fourier_transform(zeta2)
        
    if len(prev_phi_ks) < 4:  # If less than 4 previous steps are stored, use RK4
       
        phi_1_k_next, phi_2_k_next = rk4_step(phi_1_k, phi_2_k, mu_1_eq_k, mu_2_eq_k, dt, alpha, zeta_k_1, zeta_k_2)
    else:
        # Use Adams-Moulton for integration
        phi_1_k_next, phi_2_k_next = adams_moulton_step(phi_1_k, phi_2_k, mu_1_eq_k, mu_2_eq_k, alpha, zeta_k_1, zeta_k_2, prev_phi_ks, dt, compute_j_fourier)

    # Inverse Fourier Transform to get back to real space
    phi_1_next = np.real(inverse_fourier_transform(phi_1_k_next)).real
    phi_2_next = np.real(inverse_fourier_transform(phi_2_k_next)).real
    # Update fields
    phi_1, phi_2 = phi_1_next, phi_2_next
    #phi_1 = inverse_fourier_transform(phi_1_k_next).real
    #phi_2 = inverse_fourier_transform(phi_2_k_next).real
    #print(phi_1)
    #mu_1_eq = update_mu_eq(phi_1_real)

    # Store the current step and pop the oldest if there are already 4
    prev_phi_ks.append((phi_1_k_next, phi_1_k_next))
    #prev_phi_ks.append([phi_1_k_next, phi_2_k_next])
    if len(prev_phi_ks) > 4:
        prev_phi_ks.pop(0)
    # Update time
    t += dt
phi_1 = np.real(inverse_fourier_transform(phi_1_k_next))
phi_2 = np.real(inverse_fourier_transform(phi_2_k_next))

# Visualization of the final step
fig, axarr = plt.subplots(1, 2, figsize=(10, 4))
im1 = axarr[0].imshow(phi_1, cmap="RdBu_r")
axarr[0].set_title(r"$\phi_1$ at $t = T$")
fig.colorbar(im1, ax=axarr[0], fraction=0.046, pad=0.04)

im2 = axarr[1].imshow(phi_2, cmap="RdBu_r")
axarr[1].set_title(r"$\phi_2$ at $t = T$")
fig.colorbar(im2, ax=axarr[1], fraction=0.046, pad=0.04)

plt.tight_layout()
plt.savefig(f"T_chi_{chi}_alpha_{alpha}_chi'_{chi_prime}.png", dpi=600, bbox_inches='tight')
plt.show() 

#plt.savefig(f"T_chi_{chi}_alpha_{alpha}.png", dpi=1600, bbox_inches='tight')


[0, 0.49]
0
